# Investigating the coverage of the trade datasets family
## Setup SPARQL API

In [1]:
from SPARQLWrapper import SPARQLWrapper2
import pandas as pd
from IPython.display import HTML

endpoint = "https://production-drafter-ons-alpha.publishmydata.com/v1/sparql/live"
sparql = SPARQLWrapper2(endpoint)

## Retreive Data Structure Definitions
This retreives the codelist(s) for each dimension, for each dataset.

In [2]:
with open('./dataset-structure.sparql', 'r') as query_file:
    query_str = query_file.read()

sparql.setQuery(query_str)

results = pd.DataFrame(sparql.query().bindings)

## Create URI presenters
We can create presenters that will provide, for each URI, an html link to the resource (i.e. the URI itself) with the `rdfs:label` used as the text.

In [3]:
def uri_to_label(uri_column,label_column):
    return(dict(zip(results[uri_column].map(lambda x: x.value),
                    results[label_column].map(lambda x: x.value))))

labeller = {**uri_to_label('dataset_uri','dataset'),
            **uri_to_label('dimension_uri','dimension'),
            **uri_to_label('codelist_uri','codelist')}

def presenter(uri):
    return(f'<a href="{uri}">{labeller[uri]}</a> ')

def lister(presenters):
    return(presenters.str.join(''))

## Present Codelists in a matrix

Prepare a matrix of datasets vs dimensions, with each cell summarising the codelists being used.

In [4]:
codelists = results[['dataset_uri','dimension_uri','codelist_uri']].applymap(lambda x: presenter(x.value))
codelists_pivot = codelists.pivot_table(index='dataset_uri',columns='dimension_uri',values='codelist_uri',aggfunc=lister)

Sort the matrix such that the most commonly re-used dimensions are to the left hand side.

In [5]:
dimension_counts = codelists_pivot.count('rows').sort_values(ascending=False)
codelists_pivot = codelists_pivot.reindex(columns=dimension_counts.index).fillna('')
pd.set_option('max_colwidth', -1) # don't truncate cells
with open("dataset-dimensions.html", "w") as f:
    f.write(codelists_pivot.to_html(escape=False))
HTML(codelists_pivot.to_html(escape=True))

Note that although multiple datasets re-use the same common dimensions, they often use their own codelists. We know that there exist correspondances between these (e.g. BPM6 codes can be used to relate BOP and PB definitions) although we've not published the links for those yet.